In [1]:
import os
localfs_path = os.environ.get('SCRATCH_LOCAL') + '/'

In [2]:
os.environ['_JAVA_OPTIONS'] = f'-Djava.io.tmpdir={localfs_path}'

import hail as hl

hl.init(
    tmp_dir=(localfs_path+'tmp_hail_3'),
    default_reference='GRCh38'
) 

Picked up _JAVA_OPTIONS: -Djava.io.tmpdir=/localfs/4736297/
Picked up _JAVA_OPTIONS: -Djava.io.tmpdir=/localfs/4736297/


23/09/12 21:20:28 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
Running on Apache Spark version 3.3.2
SparkUI available at http://ac0520:4040
Welcome to
     __  __     <>__
    / /_/ /__  __/ /
   / __  / _ `/ / /
  /_/ /_/\_,_/_/_/   version 0.2.113-cf32652c5077
LOGGING: writing to /net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/preprocessing/oligogenic-model/hail-20230912-2120-0.2.113-cf32652c5077.log


In [3]:
from hail.plot import show
from pprint import pprint
from bokeh.layouts import gridplot
import numpy as np
hl.plot.output_notebook()
import bokeh

from bokeh.plotting import figure, output_notebook, show
output_notebook

Loading BokehJS ...

<function bokeh.io.output.output_notebook(resources=None, verbose=False, hide_banner=False, load_timeout=5000, notebook_type='jupyter')>

In [4]:
%load_ext autoreload
%autoreload 2

In [5]:
from oligogenic_model import (
    read_in_pheno_anno_pw,
    aggregate_per_burden,
    stand_burden,
    stand_with_ref,
    read_in_pheno_anno_sport,
    model_assignment,
    read_in_pheno_anno_all
)

### Use average burden from cohort to standardize

In [14]:
mt = hl.read_matrix_table(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/mts/oligogenic-model/gts_and_s.mt'
)

In [15]:
mt = mt.naive_coalesce(100)

In [16]:
mt = mt.checkpoint(localfs_path+'gts_and_s_rep.mt')

2023-09-11 19:52:16.943 Hail: INFO: wrote matrix table with 5777992 rows and 287 columns in 100 partitions to /localfs/4736297/gts_and_s_rep.mt


In [ ]:
mt = read_in_pheno_anno_sport(
    localfs_path+'gts_and_s_rep.mt',
    'gts_sport_1')

2023-09-11 19:52:20.884 Hail: INFO: Reading table without type imputation0) / 1]
  Loading field 'f0' as type str (not specified)
  Loading field 'f1' as type str (not specified)
  Loading field 'f2' as type str (not specified)
  Loading field 'f3' as type str (not specified)
  Loading field 'f4' as type str (not specified)
  Loading field 'f5' as type str (not specified)
  Loading field 'f6' as type str (not specified)
  Loading field 'f7' as type str (not specified)
  Loading field 'f8' as type str (not specified)
2023-09-11 19:52:21.763 Hail: INFO: Reading table without type imputation
  Loading field 'Gene stable ID' as type str (not specified)
  Loading field 'UniProtKB Gene Name symbol' as type str (not specified)
2023-09-11 19:52:22.846 Hail: INFO: Reading table to impute column types
2023-09-11 19:52:23.801 Hail: INFO: Finished type imputation
  Loading field 'ID' as type str (imputed)
  Loading field 'family' as type str (imputed)
  Loading field 'sex' as type str (imputed)
  

In [ ]:
#exclude low quality samples

to_exclude = ['S_7288', 'S_7289', 'S_7290', 'WGS_6827', 'WGS_6835', 'WGS_5', 'WGS_8']

mt = mt.filter_cols(
    hl.literal(to_exclude).contains(mt.s),
    keep = False
) 

mt = mt.distinct_by_col()

In [ ]:
results = aggregate_per_burden(mt, 'gts_sport_12')

results = stand_burden(results, 'gts_sport_13')

In [11]:
results = hl.read_matrix_table(localfs_path+'gts_sport_13stand_per_gene.mt')

genes = ['CHADL', 'DRD2', 'MAOA', 'PCDH10', 'HTR2A', 'SLITRK5', 'SORCS3', 'KCNQ5', 'CDH9', 'CHD8']

group, sport, model_sum, model_weits = model_assignment(results, genes)

## Now run the oligogenic model with MAF filter


In [ ]:
mt_maf =  hl.read_matrix_table(localfs_path+'gts_sport_1.mt')

In [ ]:
mt_maf = mt_maf.filter_rows(
    mt_maf.gnomad_v_3_1.freq.AF[2] < 0.0001
)

mt_maf = mt_maf.checkpoint(
    localfs_path+'mt_filt.mt'
)

In [ ]:
to_exclude = ['S_7288', 'S_7289', 'S_7290', 'WGS_6827', 'WGS_6835', 'WGS_5', 'WGS_8']

mt_maf = mt_maf.filter_cols(
    hl.literal(to_exclude).contains(mt_maf.s),
    keep = False
) 

mt_maf = mt_maf.distinct_by_col()

In [ ]:
results_maf = aggregate_per_burden(mt_maf, 'gts_sport_maf_111')
results_maf = stand_burden(results_maf, 'gts_sport_122')

In [17]:
results_maf = hl.read_matrix_table(localfs_path+'gts_sport_122stand_per_gene.mt')

In [18]:
group, sport, model_sum_maf, model_weits_maf = model_assignment(results_maf, genes)

In [11]:
from bokeh.models import Label, LabelSet

colors = bokeh.palettes.Category20[16]

y = np.linspace(0,1)
x = np.linspace(0,1,100)

from bokeh.plotting import figure, output_notebook, show

output_notebook

p = figure(plot_width=800, plot_height=800)

for o in [model_sum, model_weits]:

    for i in range(len(o)):

        start = np.min(o[i])-1
        stop = np.max(o[i])+1

        false_pos = []
        true_pos = []

        for x in np.linspace(start,stop,20000):
            false_pos.append(np.sum((o[i] > x)[group == 0])/157)
            true_pos.append(np.sum((o[i] > x)[group == 1])/46)
            
        print(i)
        print(-np.trapz(true_pos, false_pos))

        p.line(false_pos, true_pos, line_width=0.5, line_color='grey')
        
for o in [model_sum_maf, model_weits_maf]:

    for i in range(len(o)):

        start = np.min(o[i])-1
        stop = np.max(o[i])+1

        false_pos = []
        true_pos = []

        for x in np.linspace(start,stop,20000):
            false_pos.append(np.sum((o[i] > x)[group == 0])/157)
            true_pos.append(np.sum((o[i] > x)[group == 1])/46)

        print(i)
        print(-np.trapz(true_pos, false_pos))
        
        p.line(false_pos, true_pos, line_width=0.5, line_color='grey')
        
#mark the top model:

start = np.min(model_sum[0])-1
stop = np.max(model_sum[0])+1

false_pos = []
true_pos = []

for x in np.linspace(start,stop,20000):
    false_pos.append(np.sum((model_sum[0] > x)[group == 0])/157)
    true_pos.append(np.sum((model_sum[0] > x)[group == 1])/46)

p.line(false_pos, true_pos, line_width=4, line_color='#4A7A89')

sensitivity = np.array(true_pos)
specificity = 1-np.array(false_pos)

measure = sensitivity+specificity

p.circle(false_pos[8610], true_pos[8610], size=12, color="#4A7A89", alpha=1)
print('best1:'+str(false_pos[8610])+str(true_pos[8610]))

#second model:

start = np.min(model_weits_maf[0])-1
stop = np.max(model_weits_maf[0])+1

false_pos = []
true_pos = []

for x in np.linspace(start,stop,20000):
    false_pos.append(np.sum((model_weits_maf[0] > x)[group == 0])/157)
    true_pos.append(np.sum((model_weits_maf[0] > x)[group == 1])/46)

p.line(false_pos, true_pos, line_width=4, line_color='#8CAAB3')

sensitivity = np.array(true_pos)
specificity = 1-np.array(false_pos)

measure = sensitivity+specificity

p.circle(false_pos[3500], true_pos[3500], size=12, color="#8CAAB3", alpha=1)
print('best2:'+str(false_pos[3500])+str(true_pos[3500]))


p.line([0, 0.5, 1], [0, 0.5, 1])


p.xaxis.axis_label = 'false positives'
p.yaxis.axis_label = 'true positives'

p.xaxis.axis_label_text_font_size = "15pt"
p.xaxis.major_label_text_font_size = "15pt"
p.yaxis.axis_label_text_font_size = "15pt"
p.yaxis.major_label_text_font_size = "15pt"

0
0.6187344225976183
1
0.5556632511769592
2
0.5528247022985323
0
0.589171974522293
1
0.5613403489338133
2
0.5504015508169482
0
0.6044724453060093
1
0.5648019939075049
2
-0.0
0
0.6007338687344226
1
0.5673636111880366
2
-0.0
best1:0.464968152866242050.6739130434782609
best2:0.433121019108280270.6956521739130435


In [8]:
import sys
!{sys.executable} -m pip install scikit-learn

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.8/10.8 MB 9.5 MB/s eta 0:00:00:00:010:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.2/302.2 kB 13.1 MB/s eta 0:00:00

[notice] A new release of pip is available: 23.1 -> 23.2.1
[notice] To update, run: pip install --upgrade pip


In [9]:
# add confidence intervals for each model

from sklearn.metrics import roc_auc_score
from math import sqrt

def roc_auc_ci(y_true, y_score, positive=1):
    AUC = roc_auc_score(y_true, y_score)
    N1 = sum(y_true == positive)
    N2 = sum(y_true != positive)
    Q1 = AUC / (2 - AUC)
    Q2 = 2*AUC**2 / (1 + AUC)
    SE_AUC = sqrt((AUC*(1 - AUC) + (N1 - 1)*(Q1 - AUC**2) + (N2 - 1)*(Q2 - AUC**2)) / (N1*N2))
    lower = AUC - 1.96*SE_AUC
    upper = AUC + 1.96*SE_AUC
    if lower < 0:
        lower = 0
    if upper > 1:
        upper = 1
    return (lower, upper)

In [16]:
roc_auc_ci(group, model_sum[0])

(0.5230634310565297, 0.7145438799376548)

In [19]:
roc_auc_ci(group, model_sum_maf[0])

(0.5085032206212159, 0.7005801357897503)

In [18]:
show(p)

0
0.6187344225976183
1
0.5556632511769592
2
0.5528247022985323
0
0.589171974522293
1
0.5613403489338133
2
0.5504015508169482
0
0.6044724453060093
1
0.5648019939075049
2
-0.0
0
0.6007338687344226
1
0.5673636111880366
2
-0.0
best1:0.464968152866242050.6739130434782609


## Get random models (fpr)

In [44]:
all_genes = list(set(results.nearest_genes_20kb.collect()))

In [45]:
gts_genes = ['DCC', 'RBFOX', 'SLC30A9', 'DCAF4L1', 'SORCS3', 'KCNQ5', 'KCNQ-IT1', 'APOPT1', 'C14orf2', 'NAA11', 'NEGR1',
        'CHADL', 'SOX5', 'PANK2', 'COL27A1', 'PDGFB', 'CELSR3', 'OPA1', 'FBN2', 'WWC1', 'NIPBL', 
             'FN1', 'FBN2', 'SLITRK1', 'SLITRK2', 'SLITRK3', 'SLITRK4', 'SLITRK5', 'SLITRK6', 
             'HDC', 'OPRK1', 'PCDH10', 'NTSR2', 'CHD8', 'SCUBE1', 'PNKD', 'CNTNAP2', 'MOG', 
             'DRD2', 'DRD3', 'DRD4', 'DRD5', 'DAT1', 'DBH', 'HTR2A', 'TPH2', 'EAAT1', 'SAPAP3',
            'CTNNA3', 'NLGN4', 'FSCB', 'IMMP2L', 'NRXN1', 'AADAC', 'DBH', 'MAOA', 'HTR1A', 'HTR2C', 'SLC6A4',
             'TPH2', 'COL27A1', '5-HTTLPR', 'EAAT1', 'COL8A1', 'KCNE1', 'KCNE2',
         'RICTOR', 'WWC1',
        'CELSR3, NIPBL', 'FN1', 'PNKD', 'CDH26', 'CADM2', 'OPCML', 'CDH9',
         'NCAM2', 'CD47', 'CDH5', 'CADM4', 'C1QBP', 'CTTN', 'LSAMP',
         'PKP4', 'PCDH1', 'CNTNAP2', 'MBP', 'GABBR2', 'GABBR2', 'GRIK4', 'NCR1', 'FLT3', 'IL12A', 'HDAC9',
         'CD180', 'CDH26', 'NCAM2', 'NTM', 'ROBO2', 'NR2F1', 'ASH1L', 'FLT3']

In [46]:
all_genes = [g for g in all_genes if g not in gts_genes]

In [47]:
len(all_genes)

17769

In [6]:
results = hl.read_matrix_table(localfs_path+'gts_sport_13stand_per_gene.mt')

In [7]:
# randoms for the first model:

model_weits_rand = []
model_sum_rand = []
false_pos_rand = []
true_pos_rand = []
aucs = []

for i in range(1000):
    
    genes = np.random.randint(17769, size=10)
    sel_genes = [all_genes[idx] for idx in genes]
    
    group, sport, model_sum, model_weits = model_assignment(results, sel_genes)
    
    false_pos = []
    true_pos = []
    
    start = np.min(model_sum[0])-1
    stop = np.max(model_sum[0])+1
    
    for x in np.linspace(start,stop,20000):
        false_pos.append(np.sum((model_sum[0] > x)[group == 0])/157)
        true_pos.append(np.sum((model_sum[0] > x)[group == 1])/46)
        
    print(-np.trapz(true_pos, false_pos))
    
    model_weits_rand.append(model_weits)
    model_sum_rand.append(model_sum)
    false_pos_rand.append(false_pos)
    true_pos_rand.append(true_pos)
    aucs.append(-np.trapz(true_pos, false_pos))

NameError: name 'all_genes' is not defined

In [9]:
#true_pos_rand = np.array(true_pos_rand)

#np.save(
#    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/true_pos_rand_sum.npy',
#    true_pos_rand
#)

true_pos_rand = np.load(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/true_pos_rand_sum.npy'
)

#false_pos_rand = np.array(false_pos_rand)

#np.save(
#    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/false_pos_rand_sum.npy',
#    false_pos_rand
#)

false_pos_rand = np.load(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/false_pos_rand_sum.npy'
)

In [56]:
np.percentile(aucs, 95)

0.6002561617280531

In [62]:
np.percentile(aucs, 97.8)

0.6184217668235945

In [63]:
1 - 0.978 #this is the p-value

0.02200000000000002

In [ ]:
p = figure(plot_width=800, plot_height=800)

for t, f in zip(true_pos_rand[0:1000],false_pos_rand[0:1000]):
    p.line(f, t, line_width=0.1, line_color='grey', alpha=0.5)
    
p.line([0, 0.5, 1], [0, 0.5, 1], line_color = '#4A7A89', alpha = 0.5)
p.xaxis.axis_label = 'false positives'
p.yaxis.axis_label = 'true positives'

p.xaxis.axis_label_text_font_size = "20pt"
p.xaxis.major_label_text_font_size = "20pt"
p.yaxis.axis_label_text_font_size = "20pt"
p.yaxis.major_label_text_font_size = "20pt"

start = np.min(model_sum[0])-1
stop = np.max(model_sum[0])+1

false_pos = []
true_pos = []

for x in np.linspace(start,stop,20000):
    false_pos.append(np.sum((model_sum[0] > x)[group == 0])/157)
    true_pos.append(np.sum((model_sum[0] > x)[group == 1])/46)

p.line(false_pos, true_pos, line_width=4, line_color='#4A7A89')

In [ ]:
show(p)

In [ ]:
# now repeat the same with the maf weighted model:

results_maf = hl.read_matrix_table(localfs_path+'gts_sport_122stand_per_gene.mt')


model_weits_rand = []
model_sum_rand = []
false_pos_rand = []
true_pos_rand = []
aucs = []

for i in range(1000):
    
    genes = np.random.randint(17769, size=10)
    sel_genes = [all_genes[idx] for idx in genes]
    
    group, sport, model_sum, model_weits = model_assignment(results_maf, sel_genes)
    
    false_pos = []
    true_pos = []
    
    start = np.min(model_sum[0])-1
    stop = np.max(model_sum[0])+1
    
    for x in np.linspace(start,stop,20000):
        false_pos.append(np.sum((model_sum[0] > x)[group == 0])/157)
        true_pos.append(np.sum((model_sum[0] > x)[group == 1])/46)
        
    print(-np.trapz(true_pos, false_pos))
    
    model_weits_rand.append(model_weits)
    model_sum_rand.append(model_sum)
    false_pos_rand.append(false_pos)
    true_pos_rand.append(true_pos)
    aucs.append(-np.trapz(true_pos, false_pos))

In [ ]:
true_pos_rand = np.array(true_pos_rand)

np.save(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/true_pos_rand_sum_maf.npy',
    true_pos_rand
)

true_pos_rand = np.load(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/true_pos_rand_sum_maf.npy'
)

false_pos_rand = np.array(false_pos_rand)

np.save(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/false_pos_rand_sum_maf.npy',
    false_pos_rand
)

false_pos_rand = np.load(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/false_pos_rand_sum_maf.npy'
)

In [82]:
p = figure(plot_width=800, plot_height=800)

for t, f in zip(true_pos_rand[0:1000],false_pos_rand[0:1000]):
    p.line(f, t, line_width=0.1, line_color='grey', alpha=0.5)
    
p.line([0, 0.5, 1], [0, 0.5, 1], line_color = '#4A7A89', alpha = 0.5)
p.xaxis.axis_label = 'false positives'
p.yaxis.axis_label = 'true positives'

p.xaxis.axis_label_text_font_size = "15pt"
p.xaxis.major_label_text_font_size = "15pt"
p.yaxis.axis_label_text_font_size = "15pt"
p.yaxis.major_label_text_font_size = "15pt"

start = np.min(model_sum[0])-1
stop = np.max(model_sum[0])+1

false_pos = []
true_pos = []

for x in np.linspace(start,stop,20000):
    false_pos.append(np.sum((model_sum[0] > x)[group == 0])/157)
    true_pos.append(np.sum((model_sum[0] > x)[group == 1])/46)

p.line(false_pos, true_pos, line_width=4, line_color='#4A7A89')

GlyphRenderer(id='86784', ...)

In [ ]:
show(p)

### determine assignment for selected families at the optimal point:



In [105]:
mt = hl.read_matrix_table(localfs_path+'stand_with_gts_sport_4stand_per_gene_with_ref.mt')

In [109]:
mt = mt.filter_cols(hl.is_defined(mt.phenotypes.family) & (mt.phenotypes.family != '.') & (mt.phenotypes.family != 'Z'))

In [113]:
mt.count()

(10, 143)

In [111]:
genes = ['CHADL', 'DRD2', 'MAOA', 'PCDH10', 'HTR2A', 'SLITRK5', 'SORCS3', 'KCNQ5', 'CDH9', 'CHD8']

In [112]:
mt = mt.filter_rows(
        hl.literal(genes).contains(mt.nearest_genes_20kb)
    )

In [115]:
mt = mt.annotate_cols(
    n_non_ref_above_cadd_sum_0 = hl.agg.sum(mt['per_gene_stdev_above_cadd_0'])
)

In [116]:
mt = mt.annotate_cols(
    assignment = (mt['n_non_ref_above_cadd_sum_0'] > np.linspace(start,stop,20000)[8610])
)

In [117]:
mt = mt.select_cols(mt.phenotypes.family, mt.phenotypes.kinship, mt.phenotypes.phenotype, mt.assignment)

In [119]:
mt.cols().show(15)

+-------+--------+---------------------------------+-----------+------------+
| s     | family | kinship                         | phenotype | assignment |
+-------+--------+---------------------------------+-----------+------------+
| str   | str    | str                             | str       |       bool |
+-------+--------+---------------------------------+-----------+------------+
| "460" | "U"    | "P"                             | "GTS"     |      False |
| "461" | "U"    | "father"                        | "tics"    |      False |
| "462" | "U"    | "mother"                        | "."       |       True |
| "463" | "U"    | "father_brother_son"            | "GTS"     |      False |
| "465" | "U"    | "father_father"                 | "tics"    |       True |
| "466" | "W"    | "P"                             | "GTS"     |       True |
| "467" | "W"    | "sister"                        | "tics"    |       True |
| "468" | "W"    | "mother"                        | "."       |       True |
| "469" | "W"    | "father"                        | "tics"    |       True |
| "470" | "W"    | "father_parent_sibling_son"     | "tics"    |      False |
| "470" | "W"    | "father_parent_sibling_son"     | "tics"    |      False |
| "471" | "W"    | "father_parent_sibling_son"     | "GTS"     |      False |
| "472" | "W"    | "father_parent_sibling_son_son" | "tics"    |       True |
| "473" | "W"    | "father_mother"                 | "GTS"     |       True |
| "474" | "W"    | "father_sister_son"             | "GTS"     |      False |
+-------+--------+---------------------------------+-----------+------------+
showing top 15 rows

In [22]:
np.linspace(start,stop,20000)[8610]

-0.09876210987875034